### Initial setup

Imports

In [1]:
import sys, os
sys.path.append('C:/Program Files/Autodesk/FBX/FBX Python SDK/2020.3.1/samples/ImportScene')

from fbx import *
import numpy as np
import math
import struct
import heapq

Settings

In [2]:
filepath = r'./Bunny.fbx'
mesh_name = 'Mesh'
skeleton_name = 'Bunny.game_rig'
animFPS = 60

Import file

In [3]:
manager     = FbxManager.Create()
importer    = FbxImporter.Create(manager, 'myImporter')
importer.Initialize(filepath)

scene = FbxScene.Create(manager, 'myScene')

importer.Import(scene)
importer.Destroy()

Get the desired nodes

In [4]:
for i in range(scene.GetRootNode().GetChildCount()):
    node = scene.GetRootNode().GetChild(i)

    if (node.GetName() == mesh_name):
        mesh_node = node

    if (node.GetName() == skeleton_name):
        skeleton_node = node

meshAttr = mesh_node.GetNodeAttribute()
meshGeom = mesh_node.GetGeometry()

print(f'{meshAttr.GetName()} properties:')
print(f'Vertex count: {meshAttr.GetControlPointsCount()}')
print(f'Faces count:  {meshAttr.GetPolygonCount()}')
print()

Mesh.001 properties:
Vertex count: 10552
Faces count:  20972



### Building character.bin

Store: positions, normals, texcoords and normals

In [5]:
vertices    = []
normals     = []
texcoords   = []
triangles   = []

for i in range(meshAttr.GetControlPointsCount()):
    vertices.append(meshAttr.GetControlPointAt(i))

    for j in range(meshAttr.GetLayerCount()):
        leNormals   = meshAttr.GetLayer(j).GetNormals()
        leUV        = meshAttr.GetLayer(j).GetUVs()

        if leNormals:
            normals.append(leNormals.GetDirectArray().GetAt(i))
            texcoords.append(leUV.GetDirectArray().GetAt(i))

lPolygonCount = meshAttr.GetPolygonCount()
for i in range(lPolygonCount):
    lPolygonSize = meshAttr.GetPolygonSize(i)

    for j in range(lPolygonSize):
        triangles.append(meshAttr.GetPolygonVertex(i, j))

print(len(vertices))
print(len(normals))
print(len(texcoords))
print(len(triangles))

10552
10552
10552
62916


Store: bone weights and indices

In [6]:
bone_weights = []
bone_indices = []

verticesWeights = [{} for i in range(len(vertices))]
verticesBestWeights = []
lSkinCount = meshGeom.GetDeformerCount(FbxDeformer.eSkin)

for i in range(lSkinCount):
    lClusterCount = meshGeom.GetDeformer(i, FbxDeformer.eSkin).GetClusterCount()
    for j in range(lClusterCount):
        lCluster = meshGeom.GetDeformer(i, FbxDeformer.eSkin).GetCluster(j)
        
        lIndexCount = lCluster.GetControlPointIndicesCount()
        lIndices = lCluster.GetControlPointIndices()
        lWeights = lCluster.GetControlPointWeights()
        lClusterName = lCluster.GetLink().GetName()
        
        for k in range(lIndexCount):
            verticesWeights[lIndices[k]][j] = lWeights[k]

for i in range(len(verticesWeights)):
    verticesBestWeights.append(heapq.nlargest(4, verticesWeights[i].items(), key=lambda k: k[1]))
    while (len(verticesBestWeights[-1]) < 4): verticesBestWeights[-1].append((0, 0.0))

for i in range(len(verticesBestWeights)):
    bone_weights.append([verticesBestWeights[i][j][1] for j in range(4)])
    bone_indices.append([verticesBestWeights[i][j][0] for j in range(4)])

print(len(bone_weights), 'x 4')
print(len(bone_indices), 'x 4')

10552 x 4
10552 x 4


Store: rest pose

In [7]:
skeleton_nodes = []
bone_rest_positions = []
bone_rest_rotations = []

def isSkeletonBone(node):
    tmpNode = node
    while tmpNode != None and tmpNode.GetParent() != skeleton_node:
        tmpNode = tmpNode.GetParent()
    
    if tmpNode == None or tmpNode.GetParent() != skeleton_node: 
        return False
    
    return True

lPose = scene.GetPose(0)

for j in range(lPose.GetCount()):
    if isSkeletonBone(lPose.GetNode(j)) == False: 
        continue
    
    skeleton_nodes.append(lPose.GetNode(j))
    lMatrix = lPose.GetMatrix(j)

    translation = FbxVector4()
    rotation = FbxQuaternion()
    shearing = FbxVector4()
    scaling = FbxVector4()

    lMatrix.GetElements(translation, rotation, shearing, scaling)

    bone_rest_positions.append(translation)
    bone_rest_rotations.append(rotation)

print(len(bone_rest_positions))
print(len(bone_rest_rotations))

75
75


Store all in .bin file

In [8]:
with open('bunny.bin', 'wb+') as file:

    # vertices
    file.write(struct.pack('i', len(vertices)))
    for i in range(len(vertices)):
        file.write(struct.pack('fff', vertices[i][0], vertices[i][1], vertices[i][2]))

    # normals
    file.write(struct.pack('i', len(normals)))
    for i in range(len(normals)):
        file.write(struct.pack('fff', normals[i][0], normals[i][1], normals[i][2]))
   
    # texcoords
    file.write(struct.pack('i', len(texcoords)))
    for i in range(len(texcoords)):
        file.write(struct.pack('ff', texcoords[i][0], texcoords[i][1]))

    # triangles
    file.write(struct.pack('i', len(triangles)))
    for i in range(len(triangles)):
        file.write(struct.pack('H', triangles[i]))

    # bone weights
    file.write(struct.pack('i', len(bone_weights)))
    file.write(struct.pack('i', 4))
    for i in range(len(bone_weights)):
        file.write(struct.pack('ffff', bone_weights[i][0], bone_weights[i][1], bone_weights[i][2], bone_weights[i][3]))

    # bone indices
    file.write(struct.pack('i', len(bone_indices)))
    file.write(struct.pack('i', 4))
    for i in range(len(bone_indices)):
        file.write(struct.pack('HHHH', bone_indices[i][0], bone_indices[i][1], bone_indices[i][2], bone_indices[i][3]))

    # bone rest postitions  
    file.write(struct.pack('i', len(bone_rest_positions)))
    for i in range(len(bone_rest_positions)):
        file.write(struct.pack('fff', bone_rest_positions[i][0], bone_rest_positions[i][1], bone_rest_positions[i][2]))

    # bone rest rotations  
    file.write(struct.pack('i', len(bone_rest_rotations)))
    for i in range(len(bone_rest_rotations)):
        file.write(struct.pack('ffff', bone_rest_rotations[i][3], bone_rest_rotations[i][0], bone_rest_rotations[i][1], bone_rest_rotations[i][2]))

print()

### Building database.bin

In [9]:
def fbxTime2Frame(fbxTime, animFPS=animFPS):
    timeSegment = fbxTime.GetTime(FbxTime.eFrames60)
    return (timeSegment[1] * 3600 + timeSegment[2] * 60 + timeSegment[3]) * animFPS + timeSegment[4]

def GetAnimations():
    global bone_positions, bone_rotations, bone_eulers
    global range_starts, range_stops

    for i in range(scene.GetSrcObjectCount(FbxCriteria.ObjectType(FbxAnimStack.ClassId))):
        lAnimStack = scene.GetSrcObject(FbxCriteria.ObjectType(FbxAnimStack.ClassId), i)
        lAnimLayer = lAnimStack.GetSrcObject(FbxCriteria.ObjectType(FbxAnimLayer.ClassId), 0)

        nFrames = fbxTime2Frame(lAnimStack.LocalStop.Get())
        print(f'{lAnimStack.GetName()}: {nFrames} frames')

        offset = 0 if len(range_starts) == 0 else range_stops[-1]
        range_starts.append(offset)
        range_stops.append(offset + nFrames)

        bone_anim_positions = []
        bone_anim_rotations = []
        bone_anim_eulers = []

        for bone in skeleton_nodes:
            GetCurvesInfo(bone, lAnimLayer, nFrames, bone_anim_positions, bone_anim_eulers)

        if bone_positions.size == 0: 
            bone_positions = np.swapaxes(np.array(bone_anim_positions), 0, 1)
            bone_rotations = np.swapaxes(np.array(bone_anim_rotations), 0, 1)
            bone_eulers    = np.swapaxes(np.array(bone_anim_eulers), 0, 1)
        else: 
            bone_positions = np.concatenate((bone_positions, np.swapaxes(np.array(bone_anim_positions), 0, 1)))
            bone_rotations = np.concatenate((bone_rotations, np.swapaxes(np.array(bone_anim_rotations), 0, 1)))
            bone_eulers    = np.concatenate((bone_eulers,    np.swapaxes(np.array(bone_anim_eulers),    0, 1)))

def GetCurvesInfo(pNode, pAnimLayer, nFrames, bone_anim_positions, bone_anim_rotations, bone_anim_eulers):
    # Translation
    lAnimCurve = pNode.LclTranslation.GetCurve(pAnimLayer, "X")
    tX = GetCurve(lAnimCurve, nFrames)

    lAnimCurve = pNode.LclTranslation.GetCurve(pAnimLayer, "Y")
    tY = GetCurve(lAnimCurve, nFrames)

    lAnimCurve = pNode.LclTranslation.GetCurve(pAnimLayer, "Z")
    tZ = GetCurve(lAnimCurve, nFrames)

    positions = [[tX[i], tY[i], tZ[i]] for i in range(len(tX))]
    bone_anim_positions.append(positions)

    # Rotation
    lAnimCurve = pNode.LclRotation.GetCurve(pAnimLayer, "X")
    rX = GetCurve(lAnimCurve, nFrames)

    lAnimCurve = pNode.LclRotation.GetCurve(pAnimLayer, "Y")
    rY = GetCurve(lAnimCurve, nFrames)

    lAnimCurve = pNode.LclRotation.GetCurve(pAnimLayer, "Z")
    rZ = GetCurve(lAnimCurve, nFrames)
    
    eulers = [[rX[i], rY[i], rZ[i]] for i in range(len(rX))]
    bone_anim_eulers.append(eulers)

    rotMat = FbxAMatrix()
    rotMat.SetR(FbxVector4(rX[i], rY[i], rZ[i], 0.0))

    rotations = [[rotMat.GetQ()[3], rotMat.GetQ()[0], rotMat.GetQ()[1], rotMat.GetQ()[2]] for i in range(len(rX))]
    bone_anim_rotations.append(rotations)

def GetCurve(pCurve, nFrames):
    output = []

    for i in range(nFrames):
        currentTime = FbxTime()
        currentTime.SetTime(0, 0, 0, i, 0, FbxTime.eFrames60)

        output.append(pCurve.Evaluate(currentTime)[0])

    return output

# Dimensions: frame x bone x position
# value: list of pairs 
# pair: bone index and position
bone_positions = np.array([])
bone_rotations = np.array([])
bone_eulers = np.array([])
bone_angular_velocities = np.array([])
range_starts   = []
range_stops    = []


GetAnimations()
print()

bone_velocities = np.empty_like(bone_positions)
bone_angular_velocities = np.array([])

bone_velocities[1:-1] = bone_positions[2:] - bone_positions[1:-1]
bone_velocities[0]    = bone_velocities[1]
bone_velocities[-1]   = bone_velocities[-2]

bone_angular_velocities[1:-1] = bone_eulers[2:] - bone_eulers[1:-1]
bone_angular_velocities[0]    = bone_angular_velocities[1]
bone_angular_velocities[-1]   = bone_angular_velocities[-2]

print(f'bone_positions shape: {bone_positions.shape}')
print(f'bone_rotations shape: {bone_rotations.shape}')
print()

for i in range(len(range_starts)):
    print(f'AnimStack {i} range: {range_starts[i]} -> {range_stops[i]}')

print(bone_velocities[1] == bone_velocities[2])


DC_Walk_Forward: 516 frames


TypeError: GetCurvesInfo() missing 1 required positional argument: 'bone_anim_eulers'

In [ ]:
from DisplayAnimation import *

DisplayAnimation(scene)

Animation Stack Name: DC_Walk_Forward
Range: [0.0, 8.6]

Animation stack contains 1 Animation Layer(s)
AnimLayer 0
     Node Name: RootNode

     Node Name: Mesh

     Node Name: Bunny.game_rig

        TX
Key Count: 2
            Key Frame: 0.... Key Value: 0.9624683856964111 [ ? ]
            Key Frame: 516.... Key Value: 0.9624683856964111 [ ? ]
        TY
Key Count: 2
            Key Frame: 0.... Key Value: 4.785467808687827e-07 [ ? ]
            Key Frame: 516.... Key Value: 4.785467808687827e-07 [ ? ]
        TZ
Key Count: 2
            Key Frame: 0.... Key Value: 0.5524070858955383 [ ? ]
            Key Frame: 516.... Key Value: 0.5524070858955383 [ ? ]
        RX
Key Count: 2
            Key Frame: 0.... Key Value: -90.00000762939453 [ ? ]
            Key Frame: 516.... Key Value: -90.00000762939453 [ ? ]
        RY
Key Count: 2
            Key Frame: 0.... Key Value: 0.0 [ ? ]
            Key Frame: 516.... Key Value: 0.0 [ ? ]
        RZ
Key Count: 2
            Key Frame: 0.